In [8]:
import seaborn as sns
import matplotlib.pyplot as plt

from mvf_bto.data_loading import load_data
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM
from sklearn.metrics import mean_squared_error
import plotly.express as px
import numpy as np
import tqdm
import pandas as pd

In [9]:
data_path = "/Users/anoushkabhutani/PycharmProjects/10701-mvf-bto/data/2017-05-12_batchdata_updated_struct_errorcorrect.mat"


In [3]:
data = load_data(file_path= data_path, num_cells= 5)

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5/5 [00:59<00:00, 11.88s/it]


In [4]:
single_cell_data = data['b1c2']['cycles']

In [40]:
data['b1c2']['cycles'].keys()

dict_keys(['0', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', '20', '21', '22', '23', '24', '25', '26', '27', '28', '29', '30', '31', '32', '33', '34', '35', '36', '37', '38', '39', '40', '41', '42', '43', '44', '45', '46', '47', '48', '49', '50', '51', '52', '53', '54', '55', '56', '57', '58', '59', '60', '61', '62', '63', '64', '65', '66', '67', '68', '69', '70', '71', '72', '73', '74', '75', '76', '77', '78', '79', '80', '81', '82', '83', '84', '85', '86', '87', '88', '89', '90', '91', '92', '93', '94', '95', '96', '97', '98', '99', '100', '101', '102', '103', '104', '105', '106', '107', '108', '109', '110', '111', '112', '113', '114', '115', '116', '117', '118', '119', '120', '121', '122', '123', '124', '125', '126', '127', '128', '129', '130', '131', '132', '133', '134', '135', '136', '137', '138', '139', '140', '141', '142', '143', '144', '145', '146', '147', '148', '149', '150', '151', '152', '153', '154', '155', '156', 

In [11]:
df_list = []
max_cycle = 1175
for cycle_key, time_series in tqdm.tqdm(single_cell_data.items()):
    cycle_num = int(cycle_key)
    if cycle_num<1:
        continue
    df = pd.DataFrame({'t': time_series['t'], 
                       'V': time_series['V'],
                       'temp': time_series['T'],
                       'I': time_series['I'],
                       'Qd': time_series['Qd'],
                      }
                       )
    df['Cycle'] = [cycle_num/max_cycle for i in range(len(df))]
    df = df[df.I<-3.85]
    df['V_norm'] = (df.V-1.9)/(3.5-1.9)
    df['T_norm'] = (df.temp-24)/(38-24)
    df['t_norm'] = (df.t - df.t.min())/(df.t.max()-df.t.min())
    df_list.append(df)

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1176/1176 [00:03<00:00, 361.85it/s]


In [13]:
# multivariate data preparation
X_list, y_list = [], []

# split a multivariate sequence into samples
def split_sequences(sequences, n_steps):
    X, y = list(), list()
    for i in range(len(sequences)):
        # find the end of this pattern
        end_ix = i + n_steps
        # check if we are beyond the dataset
        if end_ix > len(sequences):
            break
            # gather input and output parts of the pattern
        seq_x, seq_y = sequences[i:end_ix, :-1], sequences[end_ix-1, -1]
        X.append(seq_x)
        y.append(seq_y)
    return np.array(X), np.array(y)

for df in df_list:
    df = df[::2]
    # define input sequence
    in_seq1 = df['T_norm'].values
    in_seq2 = df['Qd'].values
    in_seq3 = (df['t'].values - df['t'].values[0]) # /df['t'].max()
    # in_seq4 = df['Cycle'].values
    out_seq = df['V_norm'].values
    # convert to [rows, columns] structure
    in_seq1 = in_seq1.reshape((len(in_seq1), 1))
    in_seq2 = in_seq2.reshape((len(in_seq2), 1))
    in_seq3 = in_seq3.reshape((len(in_seq3), 1))
    # in_seq4 = in_seq4.reshape((len(in_seq4), 1))
    out_seq = out_seq.reshape((len(out_seq), 1))
    # horizontally stack columns
    dataset = np.hstack((in_seq1, in_seq2, in_seq3, out_seq))
    # choose a number of time steps
    n_steps = 5
    # convert into input/output
    X_cycle, y_cycle = split_sequences(dataset, n_steps)
    X_list.append(X_cycle)
    y_list.append(y_cycle)

In [41]:
for i in range(10):
    print(X_list[i])
    print(y_list[i])

[[[4.31227000e-01 7.30592730e-05 0.00000000e+00]
  [4.31227000e-01 7.30592730e-05 5.61166667e-03]
  [4.31227000e-01 1.37421330e-03 1.30333333e-02]
  [4.31227000e-01 1.37421330e-03 2.26066667e-02]
  [4.31227000e-01 2.49005740e-03 3.46866667e-02]]

 [[4.31227000e-01 7.30592730e-05 5.61166667e-03]
  [4.31227000e-01 1.37421330e-03 1.30333333e-02]
  [4.31227000e-01 1.37421330e-03 2.26066667e-02]
  [4.31227000e-01 2.49005740e-03 3.46866667e-02]
  [4.31227000e-01 4.08171260e-03 5.01950000e-02]]

 [[4.31227000e-01 1.37421330e-03 1.30333333e-02]
  [4.31227000e-01 1.37421330e-03 2.26066667e-02]
  [4.31227000e-01 2.49005740e-03 3.46866667e-02]
  [4.31227000e-01 4.08171260e-03 5.01950000e-02]
  [4.28188857e-01 4.08171260e-03 5.89416667e-02]]

 ...

 [[7.49831857e-01 1.06326630e+00 1.45028333e+01]
  [7.49831857e-01 1.06326630e+00 1.45062033e+01]
  [7.49831857e-01 1.06326630e+00 1.45094350e+01]
  [7.49831857e-01 1.06455120e+00 1.45123600e+01]
  [7.49831857e-01 1.06455120e+00 1.45149983e+01]]

 [[7.4

In [14]:
X_train = [item for index, item in enumerate(X_list) if index % 100 != 0]
X_test = [item for index, item in enumerate(X_list) if index % 100 == 0]

y_train = [item for index, item in enumerate(y_list) if index % 100 != 0]
y_test = [item for index, item in enumerate(y_list) if index % 100 == 0]

n_features = X_cycle.shape[2]

In [19]:
# define model
model = Sequential()
model.add(LSTM(128, return_sequences=True, input_shape=(n_steps, n_features)))
model.add(LSTM(64))
model.add(Dense(32, activation="leaky_relu"))
model.add(Dense(16))
model.add(Dense(1))

model.compile(optimizer='adam', loss='mse')

In [20]:
model.summary()

Model: "sequential_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm_4 (LSTM)               (None, 5, 128)            67584     
                                                                 
 lstm_5 (LSTM)               (None, 64)                49408     
                                                                 
 dense_6 (Dense)             (None, 32)                2080      
                                                                 
 dense_7 (Dense)             (None, 16)                528       
                                                                 
 dense_8 (Dense)             (None, 1)                 17        
                                                                 
Total params: 119,617
Trainable params: 119,617
Non-trainable params: 0
_________________________________________________________________


In [21]:
full_history = []
for epoch in tqdm.tqdm(range(500)):
    for batch in range(len(X_train)):
        X_cycle, y_cycle = X_train[batch], y_train[batch]
        history = model.fit(X_cycle, y_cycle, epochs=1, verbose=1)
        full_history.append(history)

  0%|                                                                                                                                               | 0/500 [00:00<?, ?it/s]

6/6 [==============================] - 0s 9ms/step - loss: 0.0010


6/6 [==============================] - 0s 8ms/step - loss: 0.0027


6/6 [==============================] - 0s 12ms/step - loss: 0.0017


6/6 [==============================] - 0s 8ms/step - loss: 0.0020


...

6/6 [==============================] - 0s 7ms/step - loss: 1.1631e-05


6/6 [==============================] - 0s 10ms/step - loss: 1.5696e-04


6/6 [==============================] - 0s 9ms/step - loss: 1.3072e-05


 17%|█████████████████████▏                                                                                                          | 83/500 [2:36:17<13:05:15, 112.99s/it]


KeyboardInterrupt: 

In [23]:
y_hat_list = []

for batch in range(len(X_test)):
    X_cycle, y_cycle = X_test[batch], y_test[batch]
    y_hat = model.predict(X_cycle, verbose=0)
    y_hat_list.append(y_hat)


In [24]:
import plotly.graph_objects as go

In [39]:
fig = go.Figure()
fig.add_trace(go.Scatter(x = [0,1], y = [0,1], showlegend=False))
fig.add_trace(go.Scatter(x = y_test[-2].flatten(), y = y_hat_list[-2].flatten(), showlegend=False))
fig.update_yaxes(title='Normalized Target')
fig.update_xaxes(title='Normalized Prediction')

In [30]:
fig = go.Figure()
for i in range(len(y_test)):
    fig.add_trace(go.Scatter(x = df_list[i].t, y = y_test[i].flatten(), mode='lines', name = 'data', line_color = pallete[i]))
    fig.add_trace(go.Scatter(x = df_list[i].t, y = y_hat_list[i].flatten(), mode='markers', name = 'prediction', marker_color = pallete[i]))

In [27]:
import plotly.colors

pallete = plotly.colors.qualitative.Dark24

In [33]:
fig.update_yaxes(title='Voltage [V]')
fig.update_xaxes(title='Time [min]')

In [ ]:
single_cell_data = data['b1c0']['cycles']
single_cell_data.keys()

In [ ]:
fig, ax = plt.subplots(4, 1, figsize=(5, 4 * 3))
cycles_to_plot = [10,30,50]

for cycle_num in cycles_to_plot:
    time_series = single_cell_data[str(cycle_num)]
    sns.lineplot(x=time_series['t'], y=time_series['V'], ax=ax[0], label = f"Cycle Number {cycle_num}")
    sns.lineplot(x=time_series['t'], y=time_series['T'], ax=ax[1])
    sns.lineplot(x=time_series['t'], y=time_series['I'], ax=ax[2])
    sns.lineplot(x=time_series['t'], y=time_series['Qd'], ax=ax[3])
ax[0].set_ylabel("Voltage [V]")
ax[1].set_ylabel("Temperature [C]")
ax[2].set_ylabel("Current [A]")
ax[3].set_ylabel("Discharge Capacity [Ah]")